In [1]:
import boto3
import sagemaker
import io

import pandas as pd
import numpy as np

# load training and validation dataset from Amazon S3
s3_client = boto3.client('s3')
s3_bucket_name='awsml-sagemaker-source'

response = s3_client.get_object(Bucket='awsml-sagemaker-source', Key='boston_train.csv')
response_body = response["Body"].read()
df_boston_train = pd.read_csv(io.BytesIO(response_body), header=0, delimiter=",", low_memory=False)

response = s3_client.get_object(Bucket='awsml-sagemaker-source', Key='boston_test.csv')
response_body = response["Body"].read()
df_boston_test = pd.read_csv(io.BytesIO(response_body), header=0, index_col=False, delimiter=",", low_memory=False)

# extract features and target variable into seperate datasets.
df_boston_train_target = df_boston_train.loc[:,['price']]
df_boston_train_features = df_boston_train.drop(['price'], axis=1)

df_boston_test_target = df_boston_test.loc[:,['price']]
df_boston_test_features = df_boston_test.drop(['price'], axis=1)


In [2]:
# train a linear regression model on a single feature
# the general equation for linear regression is:
# y = w1x1 + w2x2 + ... wnxn + c
#
# in case of a single feature, the equation reduces to:
# y = w1x1 + c

import tensorflow as tf
tf.reset_default_graph()

#
# define a TensorFlow graph
#

# what you will provide:
# x1 =  one-dimensional column array of features
# y_actual = one-dimensional column arrray of expected values/labels
x1 = tf.placeholder(tf.float32, [None, 1], name="x1")
y_actual = tf.placeholder(tf.float32, [None, 1], name="y_actual")

# what you  are interested in:
# w1, c weight and bias term (intercept)
w1 = tf.Variable(tf.zeros([1,1]), name="w1")
c = tf.Variable(tf.zeros([1]), name="c")

# compute y_predicged = w1x1 + c
y_predicted = tf.matmul(x1,w1) + c

# compute cost function
# MSE between predicted and actual values
mse_cost = tf.reduce_mean(tf.square(y_predicted - y_actual))

# create a root node - a gradient descent optimizer, setup to optimise the
# mse_cost function.
learning_rate = 0.000001
train_step = tf.train.GradientDescentOptimizer(learning_rate).minimize(mse_cost)

#
# execute the graph
#
with tf.Session() as sess:
    # use a global_variable_initializer node to initialize
    # variables all variables in the graph (w1 and c)
    init = tf.global_variables_initializer()
    sess.run(init)
    
    # extract CRIM feature and targer variable into arrays
    xin =  df_boston_train_features['CRIM'].values
    yin =  df_boston_train_target['price'].values
    
    xin = np.transpose([xin])
    yin = np.transpose([yin])

    # for each observaiton, evaluate the node called train_step
    # which will in turn update w1 and c so as to minimise
    # the cost function.
    best_w1 = 0.0
    best_c = 0.0
    lowest_cost = 100000.00
    
    num_epochs = 100000
    for i in range(num_epochs):
        input_dict={x1:xin, y_actual:yin}
        sess.run(train_step, feed_dict=input_dict)
        
        computed_w1 = sess.run(w1)
        computed_c = sess.run(c)
        computed_cost = sess.run(mse_cost, feed_dict=input_dict)
        
        if computed_cost < lowest_cost:
            lowest_cost = computed_cost
            best_w1 = computed_w1
            best_c = computed_c
            
        print ("End of epoch %d, w1=%f, c=%f, cost=%f" % (i, computed_w1, computed_c, computed_cost))
    print ("End of training, best_w1=%f, best_c=%f, lowest_cost=%f" % (best_w1, best_c, lowest_cost))
    

Instructions for updating:
Colocations handled automatically by placer.
End of epoch 0, w1=0.000107, c=0.000045, cost=588.338989
End of epoch 1, w1=0.000213, c=0.000090, cost=588.325623
End of epoch 2, w1=0.000320, c=0.000134, cost=588.312317
End of epoch 3, w1=0.000426, c=0.000179, cost=588.298889
End of epoch 4, w1=0.000533, c=0.000224, cost=588.285583
End of epoch 5, w1=0.000639, c=0.000269, cost=588.272278
End of epoch 6, w1=0.000745, c=0.000314, cost=588.258972
End of epoch 7, w1=0.000852, c=0.000358, cost=588.245605
End of epoch 8, w1=0.000958, c=0.000403, cost=588.232300
End of epoch 9, w1=0.001065, c=0.000448, cost=588.218933
End of epoch 10, w1=0.001171, c=0.000493, cost=588.205688
End of epoch 11, w1=0.001277, c=0.000538, cost=588.192322
End of epoch 12, w1=0.001384, c=0.000582, cost=588.179077
End of epoch 13, w1=0.001490, c=0.000627, cost=588.165710
End of epoch 14, w1=0.001596, c=0.000672, cost=588.152405
End of epoch 15, w1=0.001703, c=0.000717, cost=588.139038
End of epo

End of epoch 175, w1=0.018460, c=0.007871, cost=586.064209
End of epoch 176, w1=0.018563, c=0.007915, cost=586.051636
End of epoch 177, w1=0.018666, c=0.007960, cost=586.038940
End of epoch 178, w1=0.018769, c=0.008005, cost=586.026306
End of epoch 179, w1=0.018873, c=0.008049, cost=586.013733
End of epoch 180, w1=0.018976, c=0.008094, cost=586.001038
End of epoch 181, w1=0.019079, c=0.008139, cost=585.988403
End of epoch 182, w1=0.019182, c=0.008183, cost=585.975830
End of epoch 183, w1=0.019285, c=0.008228, cost=585.963196
End of epoch 184, w1=0.019388, c=0.008273, cost=585.950500
End of epoch 185, w1=0.019491, c=0.008317, cost=585.937927
End of epoch 186, w1=0.019594, c=0.008362, cost=585.925354
End of epoch 187, w1=0.019697, c=0.008406, cost=585.912781
End of epoch 188, w1=0.019800, c=0.008451, cost=585.900146
End of epoch 189, w1=0.019903, c=0.008496, cost=585.887512
End of epoch 190, w1=0.020006, c=0.008540, cost=585.874939
End of epoch 191, w1=0.020109, c=0.008585, cost=585.8623

End of epoch 315, w1=0.032729, c=0.014112, cost=584.331604
End of epoch 316, w1=0.032830, c=0.014157, cost=584.319580
End of epoch 317, w1=0.032931, c=0.014201, cost=584.307373
End of epoch 318, w1=0.033031, c=0.014246, cost=584.295288
End of epoch 319, w1=0.033132, c=0.014290, cost=584.283203
End of epoch 320, w1=0.033232, c=0.014335, cost=584.271179
End of epoch 321, w1=0.033333, c=0.014380, cost=584.259033
End of epoch 322, w1=0.033433, c=0.014424, cost=584.246948
End of epoch 323, w1=0.033534, c=0.014469, cost=584.234802
End of epoch 324, w1=0.033634, c=0.014513, cost=584.222778
End of epoch 325, w1=0.033735, c=0.014558, cost=584.210693
End of epoch 326, w1=0.033835, c=0.014602, cost=584.198608
End of epoch 327, w1=0.033936, c=0.014647, cost=584.186523
End of epoch 328, w1=0.034036, c=0.014691, cost=584.174500
End of epoch 329, w1=0.034136, c=0.014736, cost=584.162537
End of epoch 330, w1=0.034237, c=0.014780, cost=584.150452
End of epoch 331, w1=0.034337, c=0.014825, cost=584.1383

End of epoch 540, w1=0.054917, c=0.024109, cost=581.699341
End of epoch 541, w1=0.055014, c=0.024153, cost=581.688049
End of epoch 542, w1=0.055111, c=0.024198, cost=581.676697
End of epoch 543, w1=0.055207, c=0.024242, cost=581.665466
End of epoch 544, w1=0.055304, c=0.024286, cost=581.654175
End of epoch 545, w1=0.055400, c=0.024331, cost=581.642822
End of epoch 546, w1=0.055497, c=0.024375, cost=581.631592
End of epoch 547, w1=0.055593, c=0.024419, cost=581.620300
End of epoch 548, w1=0.055690, c=0.024464, cost=581.609070
End of epoch 549, w1=0.055786, c=0.024508, cost=581.597778
End of epoch 550, w1=0.055883, c=0.024552, cost=581.586426
End of epoch 551, w1=0.055979, c=0.024597, cost=581.575195
End of epoch 552, w1=0.056076, c=0.024641, cost=581.564026
End of epoch 553, w1=0.056172, c=0.024685, cost=581.552734
End of epoch 554, w1=0.056268, c=0.024730, cost=581.541443
End of epoch 555, w1=0.056365, c=0.024774, cost=581.530212
End of epoch 556, w1=0.056461, c=0.024818, cost=581.5189

End of epoch 712, w1=0.071279, c=0.031723, cost=579.805969
End of epoch 713, w1=0.071373, c=0.031767, cost=579.795166
End of epoch 714, w1=0.071466, c=0.031811, cost=579.784485
End of epoch 715, w1=0.071560, c=0.031856, cost=579.773743
End of epoch 716, w1=0.071653, c=0.031900, cost=579.763062
End of epoch 717, w1=0.071747, c=0.031944, cost=579.752319
End of epoch 718, w1=0.071840, c=0.031988, cost=579.741577
End of epoch 719, w1=0.071934, c=0.032032, cost=579.730896
End of epoch 720, w1=0.072028, c=0.032077, cost=579.720215
End of epoch 721, w1=0.072121, c=0.032121, cost=579.709534
End of epoch 722, w1=0.072215, c=0.032165, cost=579.698853
End of epoch 723, w1=0.072308, c=0.032209, cost=579.688171
End of epoch 724, w1=0.072401, c=0.032253, cost=579.677429
End of epoch 725, w1=0.072495, c=0.032298, cost=579.666748
End of epoch 726, w1=0.072588, c=0.032342, cost=579.656067
End of epoch 727, w1=0.072682, c=0.032386, cost=579.645447
End of epoch 728, w1=0.072775, c=0.032430, cost=579.6347

...

End of epoch 99370, w1=0.450828, c=3.703134, cost=418.757324
End of epoch 99371, w1=0.450827, c=3.703168, cost=418.756195
End of epoch 99372, w1=0.450825, c=3.703202, cost=418.755035
End of epoch 99373, w1=0.450824, c=3.703236, cost=418.753906
End of epoch 99374, w1=0.450822, c=3.703270, cost=418.752777
End of epoch 99375, w1=0.450821, c=3.703304, cost=418.751617
End of epoch 99376, w1=0.450819, c=3.703338, cost=418.750366
End of epoch 99377, w1=0.450818, c=3.703372, cost=418.749268
End of epoch 99378, w1=0.450817, c=3.703407, cost=418.748108
End of epoch 99379, w1=0.450815, c=3.703441, cost=418.746918
End of epoch 99380, w1=0.450814, c=3.703475, cost=418.745789
End of epoch 99381, w1=0.450812, c=3.703509, cost=418.744598
End of epoch 99382, w1=0.450811, c=3.703543, cost=418.743408
End of epoch 99383, w1=0.450809, c=3.703577, cost=418.742249
End of epoch 99384, w1=0.450808, c=3.703611, cost=418.741150
End of epoch 99385, w1=0.450806, c=3.703645, cost=418.739899
End of epoch 99386, w1=0

End of epoch 99513, w1=0.450619, c=3.708009, cost=418.591309
End of epoch 99514, w1=0.450618, c=3.708043, cost=418.590118
End of epoch 99515, w1=0.450617, c=3.708077, cost=418.588959
End of epoch 99516, w1=0.450615, c=3.708112, cost=418.587799
End of epoch 99517, w1=0.450614, c=3.708146, cost=418.586670
End of epoch 99518, w1=0.450612, c=3.708180, cost=418.585449
End of epoch 99519, w1=0.450611, c=3.708214, cost=418.584320
End of epoch 99520, w1=0.450609, c=3.708248, cost=418.583160
End of epoch 99521, w1=0.450608, c=3.708282, cost=418.582092
End of epoch 99522, w1=0.450606, c=3.708316, cost=418.580841
End of epoch 99523, w1=0.450605, c=3.708350, cost=418.579651
End of epoch 99524, w1=0.450603, c=3.708384, cost=418.578552
End of epoch 99525, w1=0.450602, c=3.708418, cost=418.577332
End of epoch 99526, w1=0.450600, c=3.708452, cost=418.576202
End of epoch 99527, w1=0.450599, c=3.708487, cost=418.575043
End of epoch 99528, w1=0.450598, c=3.708521, cost=418.573914
End of epoch 99529, w1=0

End of epoch 99649, w1=0.450421, c=3.712646, cost=418.433380
End of epoch 99650, w1=0.450419, c=3.712680, cost=418.432220
End of epoch 99651, w1=0.450418, c=3.712714, cost=418.431122
End of epoch 99652, w1=0.450416, c=3.712748, cost=418.429901
End of epoch 99653, w1=0.450415, c=3.712782, cost=418.428802
End of epoch 99654, w1=0.450414, c=3.712816, cost=418.427612
End of epoch 99655, w1=0.450412, c=3.712851, cost=418.426422
End of epoch 99656, w1=0.450411, c=3.712885, cost=418.425293
End of epoch 99657, w1=0.450409, c=3.712919, cost=418.424133
End of epoch 99658, w1=0.450408, c=3.712953, cost=418.422974
End of epoch 99659, w1=0.450406, c=3.712987, cost=418.421783
End of epoch 99660, w1=0.450405, c=3.713021, cost=418.420593
End of epoch 99661, w1=0.450403, c=3.713055, cost=418.419434
End of epoch 99662, w1=0.450402, c=3.713089, cost=418.418335
End of epoch 99663, w1=0.450400, c=3.713123, cost=418.417145
End of epoch 99664, w1=0.450399, c=3.713157, cost=418.415985
End of epoch 99665, w1=0

End of epoch 99785, w1=0.450222, c=3.717283, cost=418.275574
End of epoch 99786, w1=0.450221, c=3.717317, cost=418.274414
End of epoch 99787, w1=0.450219, c=3.717351, cost=418.273224
End of epoch 99788, w1=0.450218, c=3.717385, cost=418.272095
End of epoch 99789, w1=0.450216, c=3.717419, cost=418.270935
End of epoch 99790, w1=0.450215, c=3.717453, cost=418.269745
End of epoch 99791, w1=0.450213, c=3.717487, cost=418.268585
End of epoch 99792, w1=0.450212, c=3.717521, cost=418.267426
End of epoch 99793, w1=0.450211, c=3.717556, cost=418.266296
End of epoch 99794, w1=0.450209, c=3.717590, cost=418.265137
End of epoch 99795, w1=0.450208, c=3.717624, cost=418.263977
End of epoch 99796, w1=0.450206, c=3.717658, cost=418.262817
End of epoch 99797, w1=0.450205, c=3.717692, cost=418.261627
End of epoch 99798, w1=0.450203, c=3.717726, cost=418.260437
End of epoch 99799, w1=0.450202, c=3.717760, cost=418.259277
End of epoch 99800, w1=0.450200, c=3.717794, cost=418.258148
End of epoch 99801, w1=0

End of epoch 99923, w1=0.450021, c=3.721974, cost=418.115936
End of epoch 99924, w1=0.450019, c=3.722008, cost=418.114685
End of epoch 99925, w1=0.450018, c=3.722041, cost=418.113525
End of epoch 99926, w1=0.450016, c=3.722075, cost=418.112396
End of epoch 99927, w1=0.450015, c=3.722109, cost=418.111267
End of epoch 99928, w1=0.450013, c=3.722143, cost=418.110077
End of epoch 99929, w1=0.450012, c=3.722177, cost=418.108948
End of epoch 99930, w1=0.450010, c=3.722211, cost=418.107819
End of epoch 99931, w1=0.450009, c=3.722245, cost=418.106689
End of epoch 99932, w1=0.450008, c=3.722278, cost=418.105499
End of epoch 99933, w1=0.450006, c=3.722312, cost=418.104401
End of epoch 99934, w1=0.450005, c=3.722346, cost=418.103241
End of epoch 99935, w1=0.450003, c=3.722380, cost=418.102081
End of epoch 99936, w1=0.450002, c=3.722414, cost=418.100891
End of epoch 99937, w1=0.450000, c=3.722448, cost=418.099701
End of epoch 99938, w1=0.449999, c=3.722481, cost=418.098602
End of epoch 99939, w1=0

In [3]:
# use best_w1 and best_c to make predictions on all observations in the test set
predictions = df_boston_test_features['CRIM'].values * best_w1 + best_c

# compute MSE on test set
from sklearn.metrics import mean_squared_error
mse_test = mean_squared_error(np.transpose(df_boston_test_target.values), predictions)
print (mse_test)

434.61361081160874
